# 3D image of the UM Mars simulation

In [1]:
%load_ext jupyternotify

<IPython.core.display.Javascript object>

In [2]:
from pathlib import Path

import iris
import iris.quickplot as qplt
import matplotlib.pyplot as plt
import numpy as np
import pyvista as pv
from aeolus.coord import isel, regrid_3d
from aeolus.plot.pv import grid_for_scalar_cube_sph, grid_for_vector_cubes_sph
from scipy.ndimage import gaussian_filter
from aeolus.model import um
import datetime 
import time
pv.set_plot_theme("document")
pv.set_jupyter_backend("panel") 
# Enable below instead if using a headless display
# pv.set_jupyter_backend(None) 
import warnings

warnings.filterwarnings("ignore")
start_time = time.time()
directory = 'H:\\MRes\\Data\\UM\\' #Output directory for plots

In [3]:
%%time
## Load in the test files
cl = iris.load("C:\\Users\\danvi\\Documents\\example_data.nc")

Wall time: 221 ms


In [4]:
RADIUS = 3_389_500  # Planet radius [m]
z_scale = 100.0  # Scale of planet in relation to other variables
z_offset = RADIUS * 1.01  # Offset for winds

Orography

In [5]:
alt = cl.extract_cube("elevation")
grid_alt = grid_for_scalar_cube_sph(alt, z_offset=RADIUS, label="sfc_alt")
# Convert structured grid to a polydata object
poly_data_alt = grid_alt.cell_data_to_point_data().extract_geometry()
# Compute normals from the scalar data
poly_data_alt.compute_normals(cell_normals=False, inplace=True)
# Now use those normals to warp the surface
warp_alt = poly_data_alt.warp_by_scalar(scalars="sfc_alt", factor=-30)

Winds

In [6]:
wind_levels = [1000]  # [m]
# multiple levels:
# wind_levels = [2000, 5000, 10000]  # [m]

lev_constr = iris.Constraint(level_height=lambda x: x in wind_levels)

winds = [
    cl.extract_cube("x_wind").extract(lev_constr),
    cl.extract_cube("y_wind").extract(lev_constr),
    cl.extract_cube("upward_air_velocity").extract(lev_constr),
]

In [7]:
grid_vec = grid_for_vector_cubes_sph(
    *winds,
    vector_scale=RADIUS * 0.006,
    vertical_wind_scale=1e2,
    z_scale=z_scale,
    z_offset=z_offset,
    xstride=1,
    ystride=1,
    label="winds"
)

In [8]:
glyphs = grid_vec.glyph(
    orient="winds",
    scale="winds",
    tolerance=0.015 # How many vectors per unit volume to show, i.e. the density of arrows
)

Plot

In [9]:
p = pv.Plotter(window_size=[2000, 2000],off_screen=True)
p.add_mesh(warp_alt, cmap="brewer_Reds_09", show_scalar_bar=False)
p.add_mesh(glyphs, scalars="GlyphScale", show_scalar_bar=False)
p.set_position(pv.grid_from_sph_coords([230], [90], [2.1e7]).points)  # [lon], [lat], [zoom]
p.set_focus((0, 0, 0))
p.set_viewup((0, 0, 1))
p.screenshot(str(f'{directory}example.png'), transparent_background=False)
p.show(auto_close=True)

### Following code loads in pre-formatted data with Sol-ly output. 
<br> Load in data and prepare it for plotting

In [10]:
all_winds = iris.load(f"{directory}3D_render_data\\all_winds_3d*")
x_wind = iris.load(f"{directory}3D_render_data\\all_winds_3d*", "x_wind")
y_wind = iris.load(f"{directory}3D_render_data\\all_winds_3d*", "y_wind")
z_wind = iris.load(f"{directory}3D_render_data\\all_winds_3d*", "upward_air_velocity")
dust   = iris.load(f"{directory}3D_render_data\\total_dust*")


In [11]:
# dust.rename('Mass Fraction Of Dust Ukmo Dry Aerosol In Air')
dust_cube = dust.extract_cube('unknown')
dust_cube

<iris 'Cube' of unknown / (kg/kg) (time: 670; model_level_number: 51; latitude: 90; longitude: 144)>

In [12]:
print(dust_cube)
print(dust)


unknown / (kg/kg)                   (time: 670; model_level_number: 51; latitude: 90; longitude: 144)
     Dimension coordinates:
          time                           x                        -             -              -
          model_level_number             -                        x             -              -
          latitude                       -                        -             x              -
          longitude                      -                        -             -              x
     Auxiliary coordinates:
          forecast_period                x                        -             -              -
          forecast_reference_time        x                        -             -              -
          level_height                   -                        x             -              -
          sigma                          -                        x             -              -
     Attributes:
          Conventions: CF-1.7
          source: D

In [13]:
z_scale = 100.0
z_offset = RADIUS * 1.04
TOPLEV = 20
DLEV = 2  # use every 2nd level
DY = 1  # stride along y-coordinate
DX = 1  # stride along x-coordinate
dust_isosurface = [1]

In [14]:
tcoord= dust_cube.coord('time')
time_constr = iris.Constraint(time=lambda t: t.point == tcoord.units.num2date(tcoord.points[0]))
dust_cube_test=dust_cube.extract(time_constr)
dust_cube_test = dust_cube_test.extract(iris.Constraint(latitude=(lambda x: -55<=x.point<=55),longitude=(lambda x: 40<=x.point<=135))) # Select the region you want to extract dust values for
dust_cube_test

<iris 'Cube' of unknown / (kg/kg) (model_level_number: 51; latitude: 56; longitude: 38)>

In [15]:
global_qct_cntr = (
    grid_for_scalar_cube_sph(
        dust_cube_test, z_scale=z_scale, z_offset=z_offset, label="um_qct_grid"
    )
    .cell_data_to_point_data()
    .contour(isosurfaces=dust_isosurface)
)
lam_grid = grid_for_scalar_cube_sph(
    dust_cube_test[:TOPLEV:DLEV, ::DY, ::DX],
    z_scale=z_scale,
    z_offset=z_offset,
    label="um_qct_grid",
)
lam_qct_cntr = lam_grid.cell_data_to_point_data().contour()
lam_qct_cntr

PolyData (0x18b64ec35e0)
  N Cells:	21680
  N Points:	12004
  X Bounds:	-3.074e+06, 3.330e+06
  Y Bounds:	1.302e+06, 4.348e+06
  Z Bounds:	-3.610e+06, 3.610e+06
  N Arrays:	1

In [16]:
y_wind

[<iris 'Cube' of y_wind / (m s-1) (time: 670; latitude: 90; longitude: 144)>]

In [17]:
lam_dom = (
    grid_for_scalar_cube_sph(
        dust_cube_test[:TOPLEV-DLEV+1, ::1, ::1],  # show every 20th grid point
        z_scale=z_scale,
        z_offset=z_offset,
        label="lam_dom",
    )
    .extract_geometry()
    .extract_all_edges()
)

In [18]:
VIS_CONTAINER = [
    {
        # Dust concentration
        "mesh": lam_qct_cntr,
        "kwargs": {
            "cmap": "Oranges",
#             "clim": [1e-6, 1e-17], #add a limit to the dust concentrations shown
            "opacity": 0.9,
            "show_scalar_bar": False,
            "specular": 0, #default = 0
            "specular_power": 128, #Between 0-128
            "ambient": 0.5,
            "diffuse":0.4,
            "culling":"Front", #default = False, options = Front/Back
            "log_scale":False, #default = True
            "roughness":0.5, #default = 0.5, (0=rough, 1=glossy)
            "smooth_shading": False,
            "pbr":False, #defauklt
            "metallic":0  #Only use is PBR is on
        }
    },
    {
        # Grid box
        "mesh": lam_dom,
        "kwargs": {
            "style": "wireframe",
            "color": "k",
            "opacity": 0.1,
            "smooth_shading": True,
            },
        }
]

### Plot orbit for static modelling values
<br>
Following plots a gif with an orbit, but has static values.

In [20]:
p = pv.Plotter(window_size=[1000, 1000],off_screen=False)
p.add_mesh(warp_alt, cmap="brewer_Reds_09", show_scalar_bar=False)
p.add_mesh(glyphs, scalars="GlyphScale", show_scalar_bar=False)

for plot_dict in VIS_CONTAINER:
       p.add_mesh(plot_dict["mesh"], **plot_dict["kwargs"])
p.set_position(pv.grid_from_sph_coords([270], [180], [2.1e7]).points)
p.set_focus((0, 0, 0))
p.set_viewup((0, 0, 1))
# p.save_graphic('H:\\MRes\\Data\\UM\\test.pdf') # PDF if you want a better formatted image
p.screenshot(str('H:\\MRes\\Data\\UM\\test.png'), transparent_background=False)

# p.add_mesh(VIS_CONTAINER)
p.show(auto_close=False);
viewup = [0.2, 0.2, 1.4]
path = p.generate_orbital_path(factor=2.5, shift=200, viewup=viewup, n_points=4) # Change the n_points to change the amount of frames in the orbit, larger number = larger/longer gif
p.open_gif("H:\\MRes\\Data\\UM\\Mars_dust_static.gif")
# chuck = p.add_text(f'{iteration}', font_size=10, position = 'lower_left')
# chuck
legends = p.add_text(f' Winds = Intensity arrows of winds at 1km height \n Orography = Surface relief exaggerated by a factor of 30 \n Dust = Total mass mixing ratios for in selected region', font_size=14, position = 'upper_left')
legends
p.orbit_on_path(path,write_frames=True)


p.close()

In [21]:
iteration = 0
time_constr = iris.Constraint(time=lambda t: t.point == tcoord.units.num2date(tcoord.points[iteration]))
winds = [
x_wind.extract_cube("x_wind").extract(time_constr),
y_wind.extract_cube("y_wind").extract(time_constr),
z_wind.extract_cube("upward_air_velocity").extract(time_constr),
]

In [22]:
potential_framerates = 36
print("Recommended frames:")
for i in range(0,4):
    potential_framerates =potential_framerates*2
    print(potential_framerates)
print('668 - Max frame count (because of the data used, higher amounts possible but not really needed)')

Recommended frames:
72
144
288
576
668 - Max frame count (because of the data used, higher amounts possible but not really needed)


### Master cell to plot dynamic modelling alongside an orbit. <br> 
Variables to change according to your needs:
  1. 'gif_name'   | The name of the file, useful for different qualities of output
  1. 'resolution' | Resolution for PV plotter, 2000 for HD or 500 for LD
  1. 'nframe' | Frame count - higher frames = slower/longer orbit with more data points, but a larger file
  1. 'amplitude'  | Degrees of swing for the latitudinal orbit


In [34]:
%%time
%%notify

# Adjust to your preferences
gif_name = 'Mars_temp'
resolution = 2000 # resultion of window size for PV plotter
nframe = 668 # amount of frames, 36 for low-res and 578 for high-res
amplitude = 30 # intensity of the lat_orbit swing in degrees

# Don't adjust
iteration = 0 # ticker for the plotting loop

# Create a plotter object
p = pv.Plotter(off_screen=True,window_size=[resolution,resolution],notebook=False)
p.set_position(pv.grid_from_sph_coords([270], [140], [2.1e7]).points)
p.set_focus((0, 0, 0))
p.set_viewup((0, 0, 1))

RADIUS = 3_389_500  # Planet radius [m]
z_scale = 100.0
z_offset_winds = RADIUS * 1.01
z_offset_dust = RADIUS * 1.04
TOPLEV = 24 # maximum level for dust retrieval
DLEV = 1  # use every 2nd level
DY = 1  # stride along y-coordinate
DX = 1  # stride along x-coordinate
dust_isosurface = [1]


sinwave = np.linspace(-np.pi,np.pi,nframe) # Generate a simple sin wave array the size of th framerate - used for lat_orbit
lat_orbit = (np.sin(sinwave)*amplitude)+90 # change the sin wave to usable coordinates for camera position
lon_orbit = np.linspace(360,0, nframe)     # create an array for 360 orbit by the amount of frames

# Open the gif
p.open_gif(f"{directory}{gif_name}.gif")
p.add_mesh(warp_alt, cmap="brewer_Reds_09", show_scalar_bar=False, smooth_shading=False) # Add orography (not in the for-loop as it doesn't change)
legends = p.add_text(f' Winds = Intensity arrows of winds at 1km height \n Orography = Surface relief exaggerated by a factor of 30 \n Dust = Total mass mixing ratios for in selected region', font_size=14, position = 'upper_left')
legends
# Update data, camera position and write a frame for each iteration

for phase in np.linspace(0, 2 * np.pi, nframe + 1)[:nframe]:

    # Global - extract time slice
    time_constr = iris.Constraint(time=lambda t: t.point == tcoord.units.num2date(tcoord.points[iteration]))

    # Dust - extract data according to timeslice and interpret to mesh for PyVista
    dust_cube_test = dust_cube.extract(time_constr) # Extract selected time slice
    dust_cube_test = dust_cube_test.extract(iris.Constraint(latitude=(lambda x: -55<=x.point<=55),longitude=(lambda x: 40<=x.point<=135))) # Extract location slab
    
    # Dust - apply contour 
    global_qct_cntr = (grid_for_scalar_cube_sph(dust_cube_test,
                                                z_scale=z_scale, 
                                                z_offset=z_offset_dust, 
                                                label="um_qct_grid").cell_data_to_point_data().contour(isosurfaces=dust_isosurface))
    lam_grid = grid_for_scalar_cube_sph(
                                        dust_cube_test[:TOPLEV:DLEV, ::DY, ::DX],
                                        z_scale=z_scale,
                                        z_offset=z_offset_dust,
                                        label="um_qct_grid")
    lam_qct_cntr = lam_grid.cell_data_to_point_data().contour()
    lam_dom = (grid_for_scalar_cube_sph(
                                        dust_cube_test[:TOPLEV-DLEV+1, ::1, ::1],  # show every 20th grid point
                                        z_scale=z_scale,
                                        z_offset=z_offset_dust,
                                        label="lam_dom"
                                        ).extract_geometry().extract_all_edges())

    # Winds - extract data according to timeslice and interpret to mesh for PyVista
    winds = [
    x_wind.extract_cube("x_wind").extract(time_constr),
    y_wind.extract_cube("y_wind").extract(time_constr),
    z_wind.extract_cube("upward_air_velocity").extract(time_constr),
    ]
    
    # Winds - Apply glyphs to selected wind slices
    grid_vec = grid_for_vector_cubes_sph(*winds,
                                         vector_scale=RADIUS * 0.006,
                                         vertical_wind_scale=1e2,
                                         z_scale=z_scale,
                                         z_offset=z_offset_winds,
                                         xstride=1,
                                         ystride=1,
                                         label="winds")
    chuck = glyphs = grid_vec.glyph(orient="winds",scale="winds",tolerance=0.015,)
    
    # Combine dust with grid lattice 
    VIS_CONTAINER = [{
                        # Dust concentration
                        "mesh": lam_qct_cntr,
                        "kwargs": {
                            "cmap": "Oranges",
                            #"clim": [1e-6, 1e-17],
                            "opacity": 0.9,
                            "show_scalar_bar": False,
                            "specular": 0, #default = 0
                            "specular_power": 128, #Between 0-128
                            "ambient": 0.5,
                            "diffuse":0.4,
                            "culling":"Front", #default = False, options = Front/Back
                            "log_scale":False, #default = True
                            "roughness":0.5, #default = 0.5, (0=rough, 1=glossy)
                            "smooth_shading": False,
                            "pbr":False, #default
                            "metallic":0  #Only use is PBR is on
                        }
                    },
                    {
                        # Grid box
                        "mesh": lam_dom,
                        "kwargs": {
                            "style": "wireframe",
                            "color": "k",
                            "opacity": 0.1,
                            "smooth_shading": True,
                            },}]

    p.set_position(pv.grid_from_sph_coords([lon_orbit[iteration]], [lat_orbit[iteration]], [2.1e7]).points)
    
    # Now put it all together
    p.add_mesh(glyphs, scalars="GlyphScale", show_scalar_bar=False, smooth_shading=True)
    for plot_dict in VIS_CONTAINER:
       p.add_mesh(plot_dict["mesh"], **plot_dict["kwargs"])
    p.show(auto_close=False);
    # must update normals when smooth shading is enabled
    p.mesh.compute_normals(cell_normals=False, inplace=True)
    p.render()
    chuck = p.add_text(f'{iteration}', font_size=10, position = 'lower_left') # iteration number at the bottom
    chuck
    
    p.write_frame()
    p.remove_actor(p.add_mesh(glyphs, scalars="GlyphScale", show_scalar_bar=False, smooth_shading=True))
    p.remove_actor(chuck)
    iteration+=1

# Closes and finalizes movie
p.close()


<IPython.core.display.Javascript object>

Wall time: 1h 10min 28s


In [35]:
end_time = time.time()
total_time_taken = end_time-start_time

In [36]:
def timer(inp):
    mins, secs = divmod(inp, 60)
    hours, mins = divmod(mins,60)
    mins = int(mins)
    secs = int(secs)
    hours = int(hours)
    timer = datetime.time(hours,mins,secs)
    timer_test = print(f'Time taken: {timer}')
    return timer_test
timer(total_time_taken)


Time taken: 01:30:30
